## Install dependencies

In [1]:
%pip install -r requirements.txt

Note: you may need to restart the kernel to use updated packages.


ERROR: Could not open requirements file: [Errno 2] No such file or directory: 'requirements.txt'

[notice] A new release of pip is available: 24.1 -> 24.3.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [2]:
import pandas as pd
from pymongo import MongoClient
from pyspark.sql import SparkSession
import os
from pyspark.sql.functions import year
import time

## Insert data into Mongodb

The datasets are currently files in .csv format, we have to import them into Mondodb

In [3]:
'''Insert ratings.csv into MongoDB'''
# load csv file into pandas DataFrame first
df = pd.read_csv("dataset/ml-latest-small/ratings.csv")

# =specify Mongodb client, database and collection
client = MongoClient('mongodb://localhost:27017/')
db = client["test"]
collection = db["ratings"]

# convert DataFrame to a list of dictionaries (one for each row)
data = df.to_dict(orient="records")

# insert data into MongoDB
collection.insert_many(data)

InsertManyResult([ObjectId('674450bb3c85934c4a1dd083'), ObjectId('674450bb3c85934c4a1dd084'), ObjectId('674450bb3c85934c4a1dd085'), ObjectId('674450bb3c85934c4a1dd086'), ObjectId('674450bb3c85934c4a1dd087'), ObjectId('674450bb3c85934c4a1dd088'), ObjectId('674450bb3c85934c4a1dd089'), ObjectId('674450bb3c85934c4a1dd08a'), ObjectId('674450bb3c85934c4a1dd08b'), ObjectId('674450bb3c85934c4a1dd08c'), ObjectId('674450bb3c85934c4a1dd08d'), ObjectId('674450bb3c85934c4a1dd08e'), ObjectId('674450bb3c85934c4a1dd08f'), ObjectId('674450bb3c85934c4a1dd090'), ObjectId('674450bb3c85934c4a1dd091'), ObjectId('674450bb3c85934c4a1dd092'), ObjectId('674450bb3c85934c4a1dd093'), ObjectId('674450bb3c85934c4a1dd094'), ObjectId('674450bb3c85934c4a1dd095'), ObjectId('674450bb3c85934c4a1dd096'), ObjectId('674450bb3c85934c4a1dd097'), ObjectId('674450bb3c85934c4a1dd098'), ObjectId('674450bb3c85934c4a1dd099'), ObjectId('674450bb3c85934c4a1dd09a'), ObjectId('674450bb3c85934c4a1dd09b'), ObjectId('674450bb3c85934c4a1dd0

In [4]:
'''Insert movies.csv into MongoDB'''
file_path = os.path.join('dataset', 'ml-latest-small', 'movies.csv')

df = pd.read_csv(file_path)

client = MongoClient('mongodb://localhost:27017/')
db = client["test"]
collection = db["movies"]

data = df.to_dict(orient="records")
collection.insert_many(data)

InsertManyResult([ObjectId('674450be3c85934c4a1f5a68'), ObjectId('674450be3c85934c4a1f5a69'), ObjectId('674450be3c85934c4a1f5a6a'), ObjectId('674450be3c85934c4a1f5a6b'), ObjectId('674450be3c85934c4a1f5a6c'), ObjectId('674450be3c85934c4a1f5a6d'), ObjectId('674450be3c85934c4a1f5a6e'), ObjectId('674450be3c85934c4a1f5a6f'), ObjectId('674450be3c85934c4a1f5a70'), ObjectId('674450be3c85934c4a1f5a71'), ObjectId('674450be3c85934c4a1f5a72'), ObjectId('674450be3c85934c4a1f5a73'), ObjectId('674450be3c85934c4a1f5a74'), ObjectId('674450be3c85934c4a1f5a75'), ObjectId('674450be3c85934c4a1f5a76'), ObjectId('674450be3c85934c4a1f5a77'), ObjectId('674450be3c85934c4a1f5a78'), ObjectId('674450be3c85934c4a1f5a79'), ObjectId('674450be3c85934c4a1f5a7a'), ObjectId('674450be3c85934c4a1f5a7b'), ObjectId('674450be3c85934c4a1f5a7c'), ObjectId('674450be3c85934c4a1f5a7d'), ObjectId('674450be3c85934c4a1f5a7e'), ObjectId('674450be3c85934c4a1f5a7f'), ObjectId('674450be3c85934c4a1f5a80'), ObjectId('674450be3c85934c4a1f5a

## Use Apache Spark for parallel data processing

### Initial a Spark Session

In [5]:
# spark = SparkSession.builder \
#     .appName("Big-Data-Demo") \
#     .master("local[*]") \
#     .config("spark.jars.packages", "org.mongodb.spark:mongo-spark-connector_2.12:3.0.1") \
#     .config("spark.mongodb.read.connection.uri", "mongodb://127.0.0.1:27017/")  \
#     .getOrCreate() \
    
spark = SparkSession.builder \
    .appName("Big-Data-Demo") \
    .master("local[*]") \
    .config("spark.jars.packages", "org.mongodb.spark:mongo-spark-connector_2.12:3.0.1") \
    .config("spark.mongodb.read.connection.uri", "mongodb://127.0.0.1:27017/") \
    .getOrCreate() \

print(f"----------spark version: {spark.version}------------")

----------spark version: 3.5.3------------


### Load data from MongoDB

#### Load all data from a collection

In [6]:
# load all data from MongoDB
df_ratings = spark.read.format("mongo")\
    .option("uri", "mongodb://127.0.0.1:27017/")\
    .option("database", "test")\
    .option("collection", "ratings")\
    .load()    

df_movies = spark.read.format("mongo")\
    .option("uri", "mongodb://127.0.0.1:27017/test.movies")\
    .option("database", "test")\
    .option("collection", "movies")\
    .load()   

# Show the loaded data
print(f"Original Rating Data:")
print(df_ratings.show())
print(f"Original Movie Data:")
print( df_movies.show())

Original Rating Data:
+--------------------+-------+------+---------+------+
|                 _id|movieId|rating|timestamp|userId|
+--------------------+-------+------+---------+------+
|{6743f02df2b2062a...|      1|   4.0|964982703|     1|
|{6743f02df2b2062a...|      3|   4.0|964981247|     1|
|{6743f02df2b2062a...|      6|   4.0|964982224|     1|
|{6743f02df2b2062a...|     47|   5.0|964983815|     1|
|{6743f02df2b2062a...|     50|   5.0|964982931|     1|
|{6743f02df2b2062a...|     70|   3.0|964982400|     1|
|{6743f02df2b2062a...|    101|   5.0|964980868|     1|
|{6743f02df2b2062a...|    110|   4.0|964982176|     1|
|{6743f02df2b2062a...|    151|   5.0|964984041|     1|
|{6743f02df2b2062a...|    157|   5.0|964984100|     1|
|{6743f02df2b2062a...|    163|   5.0|964983650|     1|
|{6743f02df2b2062a...|    216|   5.0|964981208|     1|
|{6743f02df2b2062a...|    223|   3.0|964980985|     1|
|{6743f02df2b2062a...|    231|   5.0|964981179|     1|
|{6743f02df2b2062a...|    235|   4.0|964980

#### Make query to the database

In [7]:
# sol 1: failed, maybe because of the version of the spark
query = '{"rating": {"$gt": 4}}'
print(f"Query sent to MongoDB: {query}")

# Load filtered data
df_ratings_filtered = spark.read.format("mongo")\
    .option("uri", "mongodb://127.0.0.1:27017/")\
    .option("database", "test")\
    .option("collection", "ratings")\
    .option("query", query)\
    .load()

# Show filtered data
print("Filtered Data (movies with rating > 4):")
df_ratings_filtered.show()
query = '{"rating": {"$gt": 4}}'

Query sent to MongoDB: {"rating": {"$gt": 4}}
Filtered Data (movies with rating > 4):
+--------------------+-------+------+---------+------+
|                 _id|movieId|rating|timestamp|userId|
+--------------------+-------+------+---------+------+
|{6743f02df2b2062a...|      1|   4.0|964982703|     1|
|{6743f02df2b2062a...|      3|   4.0|964981247|     1|
|{6743f02df2b2062a...|      6|   4.0|964982224|     1|
|{6743f02df2b2062a...|     47|   5.0|964983815|     1|
|{6743f02df2b2062a...|     50|   5.0|964982931|     1|
|{6743f02df2b2062a...|     70|   3.0|964982400|     1|
|{6743f02df2b2062a...|    101|   5.0|964980868|     1|
|{6743f02df2b2062a...|    110|   4.0|964982176|     1|
|{6743f02df2b2062a...|    151|   5.0|964984041|     1|
|{6743f02df2b2062a...|    157|   5.0|964984100|     1|
|{6743f02df2b2062a...|    163|   5.0|964983650|     1|
|{6743f02df2b2062a...|    216|   5.0|964981208|     1|
|{6743f02df2b2062a...|    223|   3.0|964980985|     1|
|{6743f02df2b2062a...|    231|   5

In [8]:
# set format as "mongo" instead of "mongodb", set uri
start_time = time.time()
df_ratings_filtered = spark.read.format("mongo").option("uri", "mongodb://127.0.0.1:27017/") \
                 .option("database", "test") \
                 .option("collection", "ratings") \
                 .load()

df_ratings_filtered.filter(df_ratings_filtered['rating'] > 4)
end_time = time.time()
df_ratings_filtered.head()
print(f"Execution time: {end_time - start_time} seconds")

Execution time: 0.16145658493041992 seconds


In [9]:
# sol 2: return cursors points to rows in the collection
start_time = time.time()
client = MongoClient('mongodb://localhost:27017/')
db = client["test"]
collection = db["ratings"]

query = {"rating": {"$gt": 4}}  # Find documents where age > 25
cursors = collection.find(query)

# for doc in results:
#     print(doc)

stop_time1 = time.time()

# filtered_df = pd.DataFrame(list(cursors))
# stop_time = time.time()
# filtered_df.head()
# print(f"Time taken to fetch data from MongoDB: {stop_time1 - start_time}")
# print(f"Total time taken: {stop_time - start_time}")
# cursors = list(cursors)
# print(cursors[0]['userId', 'movieId', 'rating', 'timestamp'])

filtered_df = spark.createDataFrame(list(cursors))
filtered_df.show()

PySparkTypeError: [CANNOT_INFER_TYPE_FOR_FIELD] Unable to infer the type of the field `_id`.

In [10]:
# sol 3: get the dataframe, then filter it using pandas => worse than using MongoDB query
start_time = time.time()
df_ratings = spark.read.format("mongo")\
    .option("uri", "mongodb://127.0.0.1:27017/test.ratings")\
    .load()

df_ratings_pd = df_ratings.toPandas()
df_ratings_pd = df_ratings_pd[df_ratings_pd['rating'] > 4]

df_ratings_pd.head()
stop_time = time.time()
print(f"Time taken: {stop_time - start_time}")

Time taken: 8.536765575408936


### Spark's dataframe operations

In [11]:
# df_movies.show()
# df_ratings.show()

joined_df = df_movies.join(df_ratings, on="movieId", how="right")
print(f"movies_ratings_df:")
# print(joined_df.columns)
# print(joined_df.select("timestamp").show())
# print(type(joined_df))
joined_df.show()

movies_ratings_df:
+-------+--------------------+--------------------+--------------------+--------------------+------+---------+------+
|movieId|                 _id|              genres|               title|                 _id|rating|timestamp|userId|
+-------+--------------------+--------------------+--------------------+--------------------+------+---------+------+
|      1|{6743f02df2b2062a...|Adventure|Animati...|    Toy Story (1995)|{6743f02df2b2062a...|   4.0|964982703|     1|
|      1|{674450be3c85934c...|Adventure|Animati...|    Toy Story (1995)|{6743f02df2b2062a...|   4.0|964982703|     1|
|      3|{6743f02df2b2062a...|      Comedy|Romance|Grumpier Old Men ...|{6743f02df2b2062a...|   4.0|964981247|     1|
|      3|{674450be3c85934c...|      Comedy|Romance|Grumpier Old Men ...|{6743f02df2b2062a...|   4.0|964981247|     1|
|      6|{6743f02df2b2062a...|Action|Crime|Thri...|         Heat (1995)|{6743f02df2b2062a...|   4.0|964982224|     1|
|      6|{674450be3c85934c...|Action|

### Create a new column named "Year"

In [12]:
from pyspark.sql.functions import substring
from pyspark.sql.functions import col

joined_df = joined_df.withColumn("year", substring("title", -5, 4))
joined_df = joined_df.filter(col("year").rlike("^[12]"))
joined_df = joined_df.withColumn("year", col("year").cast("int"))

joined_df.show()
# joined_df.select("year").distinct().show()

+-------+--------------------+--------------------+--------------------+--------------------+------+----------+------+----+
|movieId|                 _id|              genres|               title|                 _id|rating| timestamp|userId|year|
+-------+--------------------+--------------------+--------------------+--------------------+------+----------+------+----+
|   1580|{674450be3c85934c...|Action|Comedy|Sci-Fi|Men in Black (a.k...|{6743f02df2b2062a...|   3.0| 964981125|     1|1997|
|   1580|{6743f02df2b2062a...|Action|Comedy|Sci-Fi|Men in Black (a.k...|{6743f02df2b2062a...|   3.0| 964981125|     1|1997|
|   2366|{674450be3c85934c...|Action|Adventure|...|    King Kong (1933)|{6743f02df2b2062a...|   4.0| 964982462|     1|1933|
|   2366|{6743f02df2b2062a...|Action|Adventure|...|    King Kong (1933)|{6743f02df2b2062a...|   4.0| 964982462|     1|1933|
|   1580|{674450be3c85934c...|Action|Comedy|Sci-Fi|Men in Black (a.k...|{6743f02df2b2062a...|   3.0| 986935244|     4|1997|
|   1580

## Train a movie recommender model

### Linear Regression Model

In [13]:
# recommender = RecommendationEngine(joined_df)

In [14]:
from pyspark.ml.feature import VectorAssembler
from pyspark.ml.regression import LinearRegression
from pyspark.ml.evaluation import RegressionEvaluator

In [15]:
feature_assembler = VectorAssembler(inputCols=["userId", "movieId"], outputCol="features")
assembled_df = feature_assembler.transform(joined_df)
(training_data, test_data) = assembled_df.randomSplit([0.8, 0.2])

model = LinearRegression(featuresCol="features", labelCol="rating", predictionCol="prediction")
lr_model = model.fit(training_data)

In [16]:
# make predictions
predictions = lr_model.transform(test_data)

# show predictions
predictions.select("features", "rating", "prediction").show()

# evaluate the model using R2 and RMSE
evaluator = RegressionEvaluator(labelCol="rating", predictionCol="prediction", metricName="rmse")
rmse = evaluator.evaluate(predictions)
print(f"Root Mean Squared Error (RMSE): {rmse}")

evaluator.setMetricName("r2")
r2 = evaluator.evaluate(predictions)
print(f"R2: {r2}")

+-----------+------+------------------+
|   features|rating|        prediction|
+-----------+------+------------------+
|  [5.0,1.0]|   4.0|3.5916200400017875|
| [18.0,1.0]|   3.5|3.5880198491852084|
| [33.0,1.0]|   3.0| 3.583865782858386|
| [43.0,1.0]|   5.0| 3.581096405307171|
| [54.0,1.0]|   3.0| 3.578050090000835|
| [57.0,1.0]|   5.0|3.5772192767354705|
| [66.0,1.0]|   4.0| 3.574726836939377|
| [68.0,1.0]|   2.5| 3.574172961429134|
| [73.0,1.0]|   4.5|3.5727882726535265|
| [98.0,1.0]|   4.5|3.5658648287754895|
|[121.0,1.0]|   4.0| 3.559495260407695|
|[144.0,1.0]|   3.5| 3.553125692039901|
|[145.0,1.0]|   5.0|3.5528487542847795|
|[156.0,1.0]|   4.0| 3.549802438978443|
|[169.0,1.0]|   4.5| 3.546202248161864|
|[179.0,1.0]|   4.0| 3.543432870610649|
|[193.0,1.0]|   2.0| 3.539555742038948|
|[214.0,1.0]|   3.0| 3.533740049181397|
|[219.0,1.0]|   3.5|3.5323553604057896|
|[220.0,1.0]|   5.0| 3.532078422650668|
+-----------+------+------------------+
only showing top 20 rows

Root Mean Squa

### ALS

In [17]:
from pyspark.ml.evaluation import RegressionEvaluator
from pyspark.ml.recommendation import ALS
from pyspark.sql import Row

ratings = joined_df.select("userId", "movieId", "rating")
(training, test) = ratings.randomSplit([0.8, 0.2])

# set cold start strategy to 'drop' to ensure we don't get NaN evaluation metrics
als = ALS(maxIter=5, regParam=0.01, userCol="userId", itemCol="movieId", ratingCol="rating",
          coldStartStrategy="drop")
model = als.fit(training)

# evaluate
predictions = model.transform(test)
evaluator = RegressionEvaluator(metricName="rmse", labelCol="rating",
                                predictionCol="prediction")
rmse = evaluator.evaluate(predictions)
print("Root-mean-square error = " + str(rmse))

# top 10 movie recommendations for each user
userRecs = model.recommendForAllUsers(10)
# top 10 user recommendations for each movie
movieRecs = model.recommendForAllItems(10)

# top 10 movie recommendations for a specified set of users
users = ratings.select(als.getUserCol()).distinct().limit(3)
userSubsetRecs = model.recommendForUserSubset(users, 10)

# top 10 user recommendations for a specified set of movies
movies = ratings.select(als.getItemCol()).distinct().limit(3)
movieSubSetRecs = model.recommendForItemSubset(movies, 10)

Root-mean-square error = 0.5891935526313823


In [18]:
print(userRecs.show())

+------+--------------------+
|userId|     recommendations|
+------+--------------------+
|     1|[{2290, 6.5960317...|
|     2|[{222, 6.820592},...|
|     3|[{26865, 7.542337...|
|     4|[{6932, 6.922081}...|
|     5|[{85, 7.7162304},...|
|     6|[{1218, 7.1544676...|
|     7|[{158872, 10.5854...|
|     8|[{5048, 9.808221}...|
|     9|[{26258, 7.517328...|
|    10|[{5666, 7.92866},...|
|    11|[{3477, 7.162686}...|
|    12|[{599, 8.141268},...|
|    13|[{115713, 8.85020...|
|    14|[{70994, 10.89416...|
|    15|[{3525, 9.351149}...|
|    16|[{861, 4.983422},...|
|    17|[{3814, 5.470887}...|
|    18|[{3272, 5.226153}...|
|    19|[{26131, 4.683866...|
|    20|[{69278, 6.561722...|
+------+--------------------+
only showing top 20 rows

None


In [22]:
userSubsetRecs.show()
users.show()

+------+--------------------+
|userId|     recommendations|
+------+--------------------+
|   463|[{103228, 6.74627...|
|   496|[{2693, 7.2756057...|
|   148|[{85, 8.026917}, ...|
+------+--------------------+

+------+
|userId|
+------+
|   463|
|   496|
|   148|
+------+



In [20]:
movieSubSetRecs.show()

+-------+--------------------+
|movieId|     recommendations|
+-------+--------------------+
|   1580|[{291, 5.5712843}...|
|   3175|[{433, 5.792061},...|
|   2366|[{77, 6.5377846},...|
+-------+--------------------+

